# INSTRM-2448

Re activate bad cobra arms.

In [1]:
import pathlib
from importlib import reload 
import matplotlib.pyplot as plt
import numpy as np
import os, fnmatch
import astropy.io.fits as pyfits
import pandas as pd

from ics.cobraCharmer.cobraCoach import visDianosticPlot

reload(visDianosticPlot)


<module 'ics.cobraCharmer.cobraCoach.visDianosticPlot' from '/software/devel/chyan/ics_cobraCharmer/python/ics/cobraCharmer/cobraCoach/visDianosticPlot.py'>

In [18]:
xml= pathlib.Path('/software/mhs/products/Linux64/pfs_instdata/1.8.2/data/pfi/modules/ALL/ALL_final_20240827_mm.xml')
vis=visDianosticPlot.VisDianosticPlot(xml=xml)


In [19]:
len(vis.badIdx)

40

In [4]:
# Show on-time
vis.calibModel.motorOntimeFwd1[vis.badIdx]

array([0.        , 0.        , 0.0562335 , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.06893137,
       0.08      , 0.        , 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.07380942, 0.        , 0.        ,
       0.07753577, 0.08      , 0.07      , 0.        , 0.        ,
       0.        , 0.        , 0.        , 0.        , 0.08      ,
       0.        , 0.04463049, 0.        , 0.        , 0.        ,
       0.        , 0.        , 0.0456551 , 0.        , 0.        ])

In [5]:
reActivateCobra = [
                #[ 1, 50],
                [ 7, 2],
                [ 8, 44],
                [26, 35],
                [32, 23],
                [ 9, 37], 
                [13, 54],
                [23, 49],
                [27, 12],
                [27, 57],
                [29, 41],
                [32, 25],
                  ]

In [6]:
# Re-activate 

for i in range(len(reActivateCobra)):
    moduleID, cobraID = reActivateCobra[i]
    vis.calibModel.setCobraStatus(cobraID, moduleId=moduleID, brokenTheta=False, brokenPhi=False, invisible=False)
    status = vis.calibModel.cobraStatus(cobraID, moduleId=moduleID)
   
    print(f'status of {moduleID}, {cobraID} is {status}')


status of 7, 2 is 1
status of 8, 44 is 1
status of 26, 35 is 1
status of 32, 23 is 1
status of 9, 37 is 1
status of 13, 54 is 1
status of 23, 49 is 1
status of 27, 12 is 1
status of 27, 57 is 1
status of 29, 41 is 1
status of 32, 25 is 1


# Set phi frequencies

In [7]:
phiFrequency = [
                #[ 1, 50, 108.1],
                [ 7,  2, 108.1],
                [ 8, 44, 144.1],
                [26, 35, 144.0],
                [32, 23, 149.0],
            ]
            

In [8]:
phiFastFwd = vis.calibModel.motorOntimeFwd2
phiFastRev = vis.calibModel.motorOntimeRev2

phiSlowFwd = vis.calibModel.motorOntimeSlowFwd2
phiSlowRev = vis.calibModel.motorOntimeSlowRev2


for i in range(len(phiFrequency)):
    moduleID, cobraID, freq2 = phiFrequency[i]
    cobraIdx = vis.calibModel.findCobraByModuleAndPositioner(moduleID, cobraID)
    freq1 = vis.calibModel.motorFreq1[cobraIdx]
    freq2 = freq2*1e3
    
    phiSlowFwd[cobraIdx] = 0.08
    phiSlowRev[cobraIdx] = 0.08
    phiFastFwd[cobraIdx] = 0.16
    phiFastRev[cobraIdx] = 0.16
    
    
    vis.calibModel.updateMotorFrequency(theta=freq1, phi=freq2, moduleId=moduleID, cobraId=cobraID)
    print(cobraIdx, moduleID, cobraID, freq1, freq2)
    print(f' {cobraIdx} Fast {vis.calibModel.motorOntimeFwd2[cobraIdx]} {vis.calibModel.motorOntimeRev2[cobraIdx]} ')
    print(f' {cobraIdx} Slow {vis.calibModel.motorOntimeSlowFwd2[cobraIdx]} {vis.calibModel.motorOntimeSlowRev2[cobraIdx]} ')
    
vis.calibModel.updateOntimes(phiFwd=phiFastFwd, phiRev=phiFastRev, fast=True)
vis.calibModel.updateOntimes(phiFwd=phiSlowFwd, phiRev=phiSlowRev, fast=False)


343 7 2 63492.06349206349 108100.0
 343 Fast 0.16 0.16 
 343 Slow 0.08 0.08 
442 8 44 62992.12598425197 144100.0
 442 Fast 0.16 0.16 
 442 Slow 0.08 0.08 
1459 26 35 63492.06349206349 144000.0
 1459 Fast 0.16 0.16 
 1459 Slow 0.08 0.08 
1789 32 23 62500.0 149000.0
 1789 Fast 0.16 0.16 
 1789 Slow 0.08 0.08 


# Set theta frequencies

In [10]:

thetaFrequency =[
        [ 9, 37, 62.7], 
        [13, 54, 59.9],
        [23, 49, 59.9],
        [27, 12, 59.9],
        [27, 57, 59.9],
        [29, 41, 50.0],
        [32, 25, 63.2],    
]

In [11]:
thetaFastFwd = vis.calibModel.motorOntimeFwd1
thetaFastRev = vis.calibModel.motorOntimeRev1

thetaSlowFwd = vis.calibModel.motorOntimeSlowFwd1
thetaSlowRev = vis.calibModel.motorOntimeSlowRev1


for i in range(len(thetaFrequency)):
    moduleID, cobraID, freq1 = thetaFrequency[i]
    cobraIdx = vis.calibModel.findCobraByModuleAndPositioner(moduleID, cobraID)

    freq1 = freq1*1e3
    freq2 = vis.calibModel.motorFreq2[cobraIdx]
    vis.calibModel.updateMotorFrequency(theta=freq1, phi=freq2, moduleId=moduleID, cobraId=cobraID)    
    
    thetaSlowFwd[cobraIdx] = 0.08
    thetaSlowRev[cobraIdx] = 0.08
    thetaFastFwd[cobraIdx] = 0.16
    thetaFastRev[cobraIdx] = 0.16
    
    print(cobraIdx, moduleID, cobraID, freq1, freq2)
    print(f' {cobraIdx} Fast {vis.calibModel.motorOntimeFwd1[cobraIdx]} {vis.calibModel.motorOntimeRev1[cobraIdx]} ')
    print(f' {cobraIdx} Slow {vis.calibModel.motorOntimeSlowFwd1[cobraIdx]} {vis.calibModel.motorOntimeSlowRev1[cobraIdx]} ')

vis.calibModel.updateOntimes(phiFwd=phiFastFwd, phiRev=phiFastRev, fast=True)
vis.calibModel.updateOntimes(phiFwd=phiSlowFwd, phiRev=phiSlowRev, fast=False)


492 9 37 62700.0 105960.26490066225
 492 Fast 0.16 0.16 
 492 Slow 0.08 0.08 
737 13 54 59900.0 106666.66666666667
 737 Fast 0.16 0.16 
 737 Slow 0.08 0.08 
1302 23 49 59900.0 106666.66666666667
 1302 Fast 0.16 0.16 
 1302 Slow 0.08 0.08 
1493 27 12 59900.0 108108.1081081081
 1493 Fast 0.16 0.16 
 1493 Slow 0.08 0.08 
1538 27 57 59900.0 102564.10256410256
 1538 Fast 0.16 0.16 
 1538 Slow 0.08 0.08 
1636 29 41 50000.0 104575.0
 1636 Fast 0.16 0.16 
 1636 Slow 0.08 0.08 
1791 32 25 63200.0 105960.26490066225
 1791 Fast 0.16 0.16 
 1791 Slow 0.08 0.08 


# Save to new XML file

In [13]:
newXml= pathlib.Path('./XML/ALL_final_20250220_mm.xml')
vis.calibModel.createCalibrationFile(newXml)

# Double check the number 

In [14]:

vis=visDianosticPlot.VisDianosticPlot(xml=newXml)


In [16]:
len(vis.badIdx)

29